# 测试分析提取伪量化算子

In [1]:
import tvm
from tvm import relay

## 测试伪量化卷积

In [5]:
x = relay.var("x", shape=[1, 3, 224, 224], dtype="int8")
w = relay.var("w", shape=[16, 3, 5, 5], dtype="int8")
zero = relay.const(0)

op = relay.op.nn.conv2d(
    relay.qnn.op.dequantize(x, relay.const(2.0), zero),
    relay.qnn.op.dequantize(w, relay.const(0.5), zero),
    kernel_size=[5, 5],
)
op = relay.qnn.op.quantize(op, relay.const(1.0), zero, out_dtype="int8")

mod = tvm.IRModule.from_expr(op)
mod.show()
fake_quantized_op_freqs = relay.analysis.list_fake_quantized_op_freqs(mod)

assert dict(fake_quantized_op_freqs) == {"nn.conv2d": 1}

## 测试伪量化 dense

In [6]:
x = relay.var("x", shape=[128, 64], dtype="int8")
w = relay.var("w", shape=[256, 64], dtype="int8")
zero = relay.const(0)

op = relay.op.nn.dense(
    relay.qnn.op.dequantize(x, relay.const(2.0), zero),
    relay.qnn.op.dequantize(w, relay.const(0.5), zero),
)
op = relay.qnn.op.quantize(op, relay.const(1.0), zero, out_dtype="int8")

mod = tvm.IRModule.from_expr(op)
mod.show()
fake_quantized_op_freqs = relay.analysis.list_fake_quantized_op_freqs(mod)

assert dict(fake_quantized_op_freqs) == {"nn.dense": 1}

## 测试伪量化多个区域

In [8]:
x = relay.var("x", shape=[128, 64], dtype="int8")
w = relay.var("w", shape=[256, 64], dtype="int8")
zero = relay.const(0)

op = relay.op.nn.dense(
    relay.qnn.op.dequantize(x, relay.const(2.0), zero),
    relay.qnn.op.dequantize(w, relay.const(0.5), zero),
)
op = relay.qnn.op.quantize(op, relay.const(1.0), zero, out_dtype="int8")

op = relay.qnn.op.dequantize(op, relay.const(2.0), relay.const(114))
op = relay.op.nn.relu(op)
op = relay.qnn.op.quantize(op, relay.const(1.0), zero, out_dtype="int8")

w2 = relay.var("w2", shape=[64, 256], dtype="int8")
op = relay.op.nn.dense(
    relay.qnn.op.dequantize(op, relay.const(1.0), zero),
    relay.qnn.op.dequantize(w2, relay.const(0.5), zero),
)
op = relay.qnn.op.quantize(op, relay.const(1.0), zero, out_dtype="int8")

# We expect to ignore this sigmoid op since it's just outside a fake
# quantized region
op = relay.op.sigmoid(op)

mod = tvm.IRModule.from_expr(op)
mod.show()
fake_quantized_op_freqs = relay.analysis.list_fake_quantized_op_freqs(mod)

assert dict(fake_quantized_op_freqs) == {"nn.dense": 2, "nn.relu": 1}

## 测试伪量化 maxpool

In [10]:
x = relay.var("x", shape=[1, 3, 224, 224], dtype="int8")

zero = relay.const(0)
x = relay.qnn.op.dequantize(x, relay.const(2.0), zero)
op = relay.op.nn.max_pool2d(x, [3, 3])
op = relay.qnn.op.quantize(op, relay.const(2.0), zero)

mod = tvm.IRModule.from_expr(op)
mod.show()
fake_quantized_op_freqs = relay.analysis.list_fake_quantized_op_freqs(mod)

assert dict(fake_quantized_op_freqs) == {"nn.max_pool2d": 1}

## 测试伪量化转置

In [11]:
x = relay.var("x", shape=[1, 3, 224, 224], dtype="int8")

zero = relay.const(0)
x = relay.qnn.op.dequantize(x, relay.const(2.0), zero)
op = relay.op.transpose(x, [1, 0, 2, 3])
op = relay.op.reshape(op, [3, -1])
op = relay.qnn.op.quantize(op, relay.const(2.0), zero)

mod = tvm.IRModule.from_expr(op)
mod.show()
fake_quantized_op_freqs = relay.analysis.list_fake_quantized_op_freqs(mod)

assert dict(fake_quantized_op_freqs) == {"transpose": 1, "reshape": 1}

## 测试伪量化 concat

In [12]:
zero = relay.const(0)
inputs = []
for i in range(4):
    inputs.append(
        relay.qnn.op.dequantize(
            relay.var("x%d" % i, shape=[1, 4], dtype="int8"), relay.const(i + 0.5), zero
        )
    )
concat = relay.op.concatenate(inputs, axis=1)
op = relay.qnn.op.quantize(concat, relay.const(3.5), zero)

mod = tvm.IRModule.from_expr(op)
mod.show()
fake_quantized_op_freqs = relay.analysis.list_fake_quantized_op_freqs(mod)

assert dict(fake_quantized_op_freqs) == {"concatenate": 1}